In [1]:
import random
import copy
import numpy as np

In [2]:
blocked_position = (2,3)
school_position = (0,4)
# number_of_states = 1104
C1 = (3,4)
C2 = (0,0)

gamma = 0.85
epsilon = 0.001

In [3]:
possible_states = []

for wol_pos_x in range(5):
    for wol_pos_y in range(5):
        for mag_pos_x in range(5):
            for mag_pos_y in range(5):
                if (mag_pos_x, mag_pos_y) != blocked_position and (wol_pos_x, wol_pos_y) != blocked_position and (mag_pos_x, mag_pos_y) != school_position:
                    possible_states.append(((wol_pos_x,wol_pos_y), (mag_pos_x, mag_pos_y), C1))
                    possible_states.append(((wol_pos_x,wol_pos_y), (mag_pos_x, mag_pos_y), C2))

In [4]:
(possible_states)

[((0, 0), (0, 0), (3, 4)),
 ((0, 0), (0, 0), (0, 0)),
 ((0, 0), (0, 1), (3, 4)),
 ((0, 0), (0, 1), (0, 0)),
 ((0, 0), (0, 2), (3, 4)),
 ((0, 0), (0, 2), (0, 0)),
 ((0, 0), (0, 3), (3, 4)),
 ((0, 0), (0, 3), (0, 0)),
 ((0, 0), (1, 0), (3, 4)),
 ((0, 0), (1, 0), (0, 0)),
 ((0, 0), (1, 1), (3, 4)),
 ((0, 0), (1, 1), (0, 0)),
 ((0, 0), (1, 2), (3, 4)),
 ((0, 0), (1, 2), (0, 0)),
 ((0, 0), (1, 3), (3, 4)),
 ((0, 0), (1, 3), (0, 0)),
 ((0, 0), (1, 4), (3, 4)),
 ((0, 0), (1, 4), (0, 0)),
 ((0, 0), (2, 0), (3, 4)),
 ((0, 0), (2, 0), (0, 0)),
 ((0, 0), (2, 1), (3, 4)),
 ((0, 0), (2, 1), (0, 0)),
 ((0, 0), (2, 2), (3, 4)),
 ((0, 0), (2, 2), (0, 0)),
 ((0, 0), (2, 4), (3, 4)),
 ((0, 0), (2, 4), (0, 0)),
 ((0, 0), (3, 0), (3, 4)),
 ((0, 0), (3, 0), (0, 0)),
 ((0, 0), (3, 1), (3, 4)),
 ((0, 0), (3, 1), (0, 0)),
 ((0, 0), (3, 2), (3, 4)),
 ((0, 0), (3, 2), (0, 0)),
 ((0, 0), (3, 3), (3, 4)),
 ((0, 0), (3, 3), (0, 0)),
 ((0, 0), (3, 4), (3, 4)),
 ((0, 0), (3, 4), (0, 0)),
 ((0, 0), (4, 0), (3, 4)),
 

In [5]:
def is_legal(state):
    if state[0] <= 4:
        if state != blocked_position:
            return 1
        else:
            return 0
    
    return -1

In [6]:
def sum_action_reward(state, U, policy):
    utility = 0.95*U[((policy[state][0], policy[state][1]), state[1], state[2])] + 0.05*U[state]
    return utility

In [7]:
def reward(state):
    wol_pos = state[0]
    mag_pos = state[1]
    jean_pos = state[2]
    
    if wol_pos == mag_pos and mag_pos == jean_pos:
        return -15
    else:
        if mag_pos == jean_pos:
            return -20
        
        if wol_pos == jean_pos:
            return 20
    
    return 0

In [8]:
def policy_evaluation(policy, U):
    for state in possible_states:
        U[state] = reward(state) + gamma*sum_action_reward(state, U, policy)
    
    return U

In [9]:
def wol_pos_reachable(old_pos, new_pos):
    if abs(old_pos[0] - new_pos[0]) == 1 and abs(old_pos[1] - new_pos[1]) == 0:
        return True
    
    if abs(old_pos[0] - new_pos[0]) == 0 and abs(old_pos[1] - new_pos[1]) == 1:
        return True
    
    if abs(old_pos[0] - new_pos[0]) == 0 and abs(old_pos[1] - new_pos[1]) == 0:
        return True
    
    return False

In [10]:
def is_reachable(state_a, state_b):
    old_wol_pos = state_a[0]
    old_mag_pos = state_a[1]
    old_jean_pos = state_a[2]
    
    new_wol_pos = state_b[0]
    new_mag_pos = state_b[1]
    new_jean_pos = state_b[2]
    
    return wol_pos_reachable(old_wol_pos, new_wol_pos) and wol_pos_reachable(old_mag_pos, new_mag_pos)

In [11]:
def get_max_utility_action(state, U):
    reachable_states = []
    
    for s in possible_states:
        if is_reachable(state, s):
            reachable_states.append(s)
    
    
    max_utility = 0
    max_utility_action = (0,0)
    
    wol_pos_x = state[0][0]
    wol_pos_y = state[0][1]
    
    mag_pos_x = state[1][0]
    mag_pos_y = state[1][1]
    
    jean_pos_x = state[2][0]
    jean_pos_y = state[2][1]
    
    
    # Each reachable state is reached by a unique action
    # However, when we perform that action, other states can also be reached unintentionally with some probability
    # We divide the total action into 3 subactions: Wolverine subaction, Magneto Subaction and Jean Subaction
    # Each subaction can either succeed or fail. 
    # Thus, total 8 actions are possible
    
    for s in reachable_states:
        temp_wol_pos_x = s[0][0]
        temp_wol_pos_y = s[0][1]

        temp_mag_pos_x = s[1][0]
        temp_mag_pos_y = s[1][1]

        temp_jean_pos_x = s[2][0]
        temp_jean_pos_y = s[2][1]
        
        
        temp_utility = 0
        temp_utility = temp_utility + 0.95*(0.95/4)*0.8*U[((temp_wol_pos_x, temp_wol_pos_y), (temp_mag_pos_x, temp_mag_pos_y), (temp_jean_pos_x, temp_jean_pos_y))]    # 111
        temp_utility = temp_utility + 0.95*(0.95/4)*0.2*U[((temp_wol_pos_x, temp_wol_pos_y), (temp_mag_pos_x, temp_mag_pos_y), (jean_pos_x, jean_pos_y))]    # 110
        temp_utility = temp_utility + 0.95*(0.05)*0.8*U[((temp_wol_pos_x, temp_wol_pos_y), (mag_pos_x, mag_pos_y), (temp_jean_pos_x, temp_jean_pos_y))]    # 101
        temp_utility = temp_utility + 0.95*(0.05)*0.2*U[((temp_wol_pos_x, temp_wol_pos_y), (mag_pos_x, mag_pos_y), (jean_pos_x, jean_pos_y))]    # 100
        temp_utility = temp_utility + 0.05*(0.95/4)*0.8*U[((wol_pos_x, wol_pos_y), (temp_mag_pos_x, temp_mag_pos_y), (temp_jean_pos_x, temp_jean_pos_y))]  # 011 Wolverine stays put
        temp_utility = temp_utility + 0.05*(0.95/4)*0.2*U[((wol_pos_x, wol_pos_y), (temp_mag_pos_x, temp_mag_pos_y), (jean_pos_x, jean_pos_y))]  # 010 Wolverine and Magneto stays put
        temp_utility = temp_utility + 0.05*(0.05)*0.8*U[((wol_pos_x, wol_pos_y), (mag_pos_x, mag_pos_y), (temp_jean_pos_x, temp_jean_pos_y))]  # 001 Wolverine, Magneto, Jean stays put
        temp_utility = temp_utility + 0.05*(0.05)*0.2*U[((wol_pos_x, wol_pos_y), (mag_pos_x, mag_pos_y), (jean_pos_x, jean_pos_y))]    # 000 
        
        if max_utility < temp_utility:
            max_utility = temp_utility
            max_utility_action = s[0]      # doubtful
        
    
    return (max_utility, max_utility_action)

In [12]:
policy = {}

for state in possible_states:
    new_state = (state[0][0]+1, state[0][1])
    
#     result = is_legal(new_state)
    
    if is_legal(new_state) == 1:
        policy[state] = new_state
    else:
        policy[state] = (state[0][0] - 1, state[0][1])

U = {}
for state in possible_states:
    U[state] = 0

unchanged = True
for i in range(25):
    print(i)
    U = policy_evaluation(policy, U)
    unchanged = True

    for state in possible_states:
        (max_utility, max_utility_action) = get_max_utility_action(state, U)
        policy_utility = 0.95*U[((policy[state][0], policy[state][1]), state[1], state[2])] + 0.05*U[state]
        if max_utility > policy_utility:
            policy[state] = max_utility_action
            unchanged = False
    if unchanged:
        break

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24


In [13]:
U

{((0, 0), (0, 0), (3, 4)): 0.0,
 ((0, 0), (0, 0), (0, 0)): -98.28021901477918,
 ((0, 0), (0, 1), (3, 4)): 0.0,
 ((0, 0), (0, 1), (0, 0)): 131.0402920197056,
 ((0, 0), (0, 2), (3, 4)): 0.0,
 ((0, 0), (0, 2), (0, 0)): 131.0402920197056,
 ((0, 0), (0, 3), (3, 4)): 0.0,
 ((0, 0), (0, 3), (0, 0)): 131.0402920197056,
 ((0, 0), (1, 0), (3, 4)): 0.0,
 ((0, 0), (1, 0), (0, 0)): 131.0402920197056,
 ((0, 0), (1, 1), (3, 4)): 0.0,
 ((0, 0), (1, 1), (0, 0)): 131.0402920197056,
 ((0, 0), (1, 2), (3, 4)): 0.0,
 ((0, 0), (1, 2), (0, 0)): 131.0402920197056,
 ((0, 0), (1, 3), (3, 4)): 0.0,
 ((0, 0), (1, 3), (0, 0)): 131.0402920197056,
 ((0, 0), (1, 4), (3, 4)): 0.0,
 ((0, 0), (1, 4), (0, 0)): 131.0402920197056,
 ((0, 0), (2, 0), (3, 4)): 0.0,
 ((0, 0), (2, 0), (0, 0)): 131.0402920197056,
 ((0, 0), (2, 1), (3, 4)): 0.0,
 ((0, 0), (2, 1), (0, 0)): 131.0402920197056,
 ((0, 0), (2, 2), (3, 4)): 0.0,
 ((0, 0), (2, 2), (0, 0)): 131.0402920197056,
 ((0, 0), (2, 4), (3, 4)): 0.0,
 ((0, 0), (2, 4), (0, 0)): 131.

In [14]:
def update_wol_position(wol_pos_x, wol_pos_y, mag_pos_x, mag_pos_y, jean_pos_x, jean_pos_y):
    max_utility = -1
    max_utility_neighbor = ()
    if wol_pos_x < 4 and (wol_pos_x+1, wol_pos_y) != blocked_position:
        if U[(wol_pos_x+1, wol_pos_y),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)] > max_utility:
            max_utility = U[(wol_pos_x+1, wol_pos_y),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)]
            max_utility_neighbor = (wol_pos_x+1, wol_pos_y)
    
    if wol_pos_x > 0 and (wol_pos_x-1, wol_pos_y) != blocked_position:
        if U[(wol_pos_x-1, wol_pos_y),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)] > max_utility:
            max_utility = U[(wol_pos_x-1, wol_pos_y),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)]
            max_utility_neighbor = (wol_pos_x-1, wol_pos_y)
    
    if wol_pos_y < 4 and (wol_pos_x, wol_pos_y+1) != blocked_position:
        if U[(wol_pos_x, wol_pos_y+1),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)] > max_utility:
            max_utility = U[(wol_pos_x, wol_pos_y+1),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)]
            max_utility_neighbor = (wol_pos_x, wol_pos_y+1)
    
    if wol_pos_y > 0 and (wol_pos_x, wol_pos_y-1) != blocked_position:
        if U[(wol_pos_x, wol_pos_y-1),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)] > max_utility:
            max_utility = U[(wol_pos_x, wol_pos_y-1),(mag_pos_x, mag_pos_y),(jean_pos_x, jean_pos_y)]
            max_utility_neighbor = (wol_pos_x, wol_pos_y-1)
    
    return max_utility_neighbor

In [15]:
def update_mag_position(mag_pos_x, mag_pos_y):
    temp = random.random()
    if temp < 0.05:
        return (mag_pos_x, mag_pos_y)
    
    valid_positions = []
    if mag_pos_x < 4 and (mag_pos_x+1, mag_pos_y) != blocked_position and (mag_pos_x+1, mag_pos_y) != school_position:
        valid_positions.append((mag_pos_x+1, mag_pos_y))
    
    if mag_pos_x > 0 and (mag_pos_x-1, mag_pos_y) != blocked_position and (mag_pos_x-1, mag_pos_y) != school_position:
        valid_positions.append((mag_pos_x-1, mag_pos_y))
    
    if mag_pos_y < 4 and (mag_pos_x, mag_pos_y+1) != blocked_position and (mag_pos_x, mag_pos_y+1) != school_position:
        valid_positions.append((mag_pos_x, mag_pos_y+1))
    
    if mag_pos_y > 0 and (mag_pos_x, mag_pos_y-1) != blocked_position and (mag_pos_x, mag_pos_y-1) != school_position:
        valid_positions.append((mag_pos_x, mag_pos_y-1))
    
    index = random.randint(0, len(valid_positions)-1)
    
    return valid_positions[index]
    

In [16]:
def update_jean_position(jean_pos_x, jean_pos_y):
    if random.random() < 0.8:
        return (jean_pos_x, jean_pos_y)
    
    if (jean_pos_x, jean_pos_y) == C1:
        return C2
    
    return C1

In [25]:
def perform_policy_iteration():
    grid = [[0,0,0,0,0],
            [0,0,0,0,0],
            [0,0,0,0,0],
            [0,0,0,0,0],
            [0,0,0,0,0]]

    grid[blocked_position[0]][blocked_position[1]] = 'B'

    wol_pos_x = random.randint(0,4)
    wol_pos_y = random.randint(0,4)

    mag_pos_x = random.randint(0,4)
    mag_pos_y = random.randint(0,4)
    
    while((wol_pos_x, wol_pos_y) == blocked_position):
        wol_pos_x = random.randint(0,4)
        wol_pos_y = random.randint(0,4)

    while((mag_pos_x, mag_pos_y) == blocked_position or (mag_pos_x, mag_pos_y) == school_position):
        mag_pos_x = random.randint(0,4)
        mag_pos_y = random.randint(0,4)
        
    jean_pos_x = C1[0]
    jean_pos_y = C1[1]

    while True:

        if (wol_pos_x, wol_pos_y) == (mag_pos_x, mag_pos_y):
            print('Magneto captured Wolverine')
            return 'Magneto captured Wolverine'
            break

        if (wol_pos_x, wol_pos_y) == (jean_pos_x, jean_pos_y):
            print('Wolverine captured Jean')
            return 'Wolverine captured Jean'
            break

        if (mag_pos_x, mag_pos_y) == (jean_pos_x, jean_pos_y):
            print('Magneto captured Jean')
            return 'Magneto captured Jean'
            break

        grid[wol_pos_x][wol_pos_y] = 'W'
        grid[mag_pos_x][mag_pos_y] = 'M'
        grid[jean_pos_x][jean_pos_y] = 'J'

        print(np.array(grid))
        print('\n')

        grid[wol_pos_x][wol_pos_y] = 0
        grid[mag_pos_x][mag_pos_y] = 0
        grid[jean_pos_x][jean_pos_y] = 0

        (wol_pos_x, wol_pos_y) = update_wol_position(wol_pos_x, wol_pos_y, mag_pos_x, mag_pos_y, jean_pos_x, jean_pos_y)
        (mag_pos_x, mag_pos_y) = update_mag_position(mag_pos_x, mag_pos_y)
        (jean_pos_x, jean_pos_y) = update_jean_position(jean_pos_x, jean_pos_y)
    
    

    

In [32]:
result_dict = {}
result_dict['Magneto captured Wolverine'] = 0
result_dict['Wolverine captured Jean'] = 0
result_dict['Magneto captured Jean'] = 0

for i in range(10000):
    result = perform_policy_iteration()

    result_dict[result] += 1 
    
    print('----------------------------------------------------')

[['0' '0' '0' '0' '0']
 ['0' 'W' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' 'M' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'W' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'W' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' 'M' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'W' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' 'M' 'B' '0']
 ['0' '0' '0' 'W' '0']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' 'M' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'W' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' 'M' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' 'W' 'J']
 ['0' '0' '0' '0' '0']]


Wolverine captured Jean
----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['M' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['W'

[['M' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' 'W' 'J']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['M' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['M' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['M' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' 'W']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'M' '0' 'B' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']]


[['J' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' 

 ['0' '0' '0' '0' 'W']]


[['J' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']]


Magneto captured Jean
----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']
 ['M' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' 'W']
 ['M' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'M' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' 'W' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['0' '0' 'W' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'M' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' 'W' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0



[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' 'M' 'J']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' 'W']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']]


[['J' '0' '0' 'W' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' 'M' '0' '0']]


[['J' '0' 'W' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'M' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' 'W' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['W' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'M' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['W' 'M' '0' '0' '0']
 ['0' '0


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['M' '0' '0' '0' 'J']
 ['0' 'W' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['M' '0' 'W' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['M' '0' '0' 'W' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['M' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' 'W']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['M' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'W']
 ['M' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'M' '0' '0' 'W']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0'

...

 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'M']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'W' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' 'W' 'J']
 ['0' '0' '0' '0' '0']]


Wolverine captured Jean
----------------------------------------------------
Magneto captured Jean
----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' 'M' '0' 'W' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['M' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' 'W']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


Wolverine captured Jean
----------------------------------------------------
[['0' '0' '0' 'M' '0']
 ['0' '0' '0' '0' '0']
 ['W' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' 

 ['0' '0' '0' '0' '0']]


Magneto captured Jean
----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['M' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' 'W' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'M' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' 'W' '0']]


[['0' '0' '0' '0' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' 'W']]


Wolverine captured Jean
----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' 'W' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' 'M' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'W' '0' 'J']
 ['0' '0' '0' 'M' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' 'W' 'J']
 ['0' '0' '0' '0' 'M']]


Magneto captured Wolverine
----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['W' '0' '

----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' 'W' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'M']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' 'W' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' 'W' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'M']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' 'W']]


Wolverine captured Jean
----------------------------------------------------
Wolverine captured Jean
----------------------------------------------------
[['W' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' 'M' '0' '0']]


[['J' '0' '0' '0' '0']
 ['W' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'M' '0' '0' '0']]


Wolverine captured Jean
----------------------------------------------------
[['0' 'M

 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' 'W' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' 'M' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'W']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' 'M' '0' '0']]


[['J' '0' '0' '0' 'W']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' 'M' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' 'W' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' 'W' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['M' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' 'W' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'M' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


Wolverine captured Jean
----------------------------------------------------
[['0' '0' '0' 'M' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'W' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 [

----------------------------------------------------
[['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'W' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' 'M' '0' '0' '0']]


Magneto captured Wolverine
----------------------------------------------------
[['0' 'W' '0' 'M' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' '0' '0']
 ['0' 'W' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['0' '0' '0' 'M' '0']
 ['0' '0' '0' '0' '0']
 ['0' 'W' '0' 'B' '0']
 ['0' '0' '0' '0' 'J']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' 'M' '0']
 ['0' '0' '0' 'B' '0']
 ['0' 'W' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' '0' '0' '0' 'M']
 ['0' 'W' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['J' '0' '0' '0' '0']
 ['0' 'W' '0' '0' 'M']
 ['0' '0' '0' 'B' '0']
 ['0' '0' '0' '0' '0']
 ['0' '0' '0' '0' '0']]


[['0' 'W' '0' '0' '0']
 ['0' '0' '0' 'M' 

In [33]:
result_dict

{'Magneto captured Wolverine': 1497,
 'Wolverine captured Jean': 6733,
 'Magneto captured Jean': 1770}